In [1]:
using LinearAlgebra
using Plots
using Roots
using Printf
using Random
using Colors
using FileIO

# Interpolation Problem

Construct the interpolant
$$
P(x) = \sum_{j=0}^n a_j x^j
$$
by solving
$$
\begin{bmatrix}
1 & x_0 & x_0^2 &\cdots & x_0^n\\
1 & x_1 & x_1^2 &\cdots & x_1^n\\
\vdots & \vdots & \cdots & \vdots\\
1 & x_n & x_n^2 &\cdots & x_n^n\\
\end{bmatrix}
\begin{pmatrix}
a_0\\
a_1\\
\vdots\\
a_n
\end{pmatrix}=
\begin{pmatrix}
f_0\\
f_1\\
\vdots\\
f_n
\end{pmatrix}
$$
Investigate what happens when a small amount of noise is introduced into the data, $f_j$.

In [2]:
n = 20; #really n+1 in the above system.
xnodes = range(0, 2*π,length=n);
fnodes = sin.(xnodes);

# build up matrix
V = zeros(n,n)
for j in 1:n
    V[j,:] = xnodes[j].^(0:1:(n-1))
end

In [3]:
V

20×20 Matrix{Float64}:
 1.0  0.0        0.0         0.0        …     0.0              0.0
 1.0  0.330694   0.109358    0.0361642        2.23704e-9       7.39774e-10
 1.0  0.661388   0.437434    0.289314         0.000586425      0.000387855
 1.0  0.992082   0.984226    0.976433         0.866673         0.859811
 1.0  1.32278    1.74974     2.31451        153.728          203.348
 1.0  1.65347    2.73396     4.52052    …  8533.61         14110.1
 1.0  1.98416    3.93691     7.81147          2.27193e5        4.50789e5
 1.0  2.31486    5.35857    12.4043           3.64282e6        8.43261e6
 1.0  2.64555    6.99894    18.5161           4.02988e7        1.06613e8
 1.0  2.97625    8.85804    26.3637           3.35767e8        9.99325e8
 1.0  3.30694   10.9358     36.1642     …     2.23704e9        7.39774e9
 1.0  3.63763   13.2324     48.1345           1.24377e10       4.52439e10
 1.0  3.96833   15.7476     62.4917           5.95573e10       2.36343e11
 1.0  4.29902   18.4816     79.4527    

In [4]:
a=V\fnodes

20-element Vector{Float64}:
  0.0
  0.9999999999594461
  4.4435448412227477e-10
 -0.1666666687885417
  5.932511170964681e-9
  0.008333322369306019
  1.4300443004037642e-8
 -0.0001984263964922748
  9.883063220752317e-9
  2.7502760094449225e-6
  2.323643464212078e-9
 -2.5816575738381198e-8
  1.9298096394047384e-10
  1.238942185803297e-10
  5.045694658131221e-12
 -1.2177595107324158e-12
  1.7196794392933133e-14
  4.2303879462631865e-15
 -2.38630966995021e-16
  3.907569212514947e-18

Noise takes the form
$$
\tilde{f}_i = f_i(1 + \epsilon_i)
$$
where $\epsilon_i$ are small Gaussian random variables.

In [6]:
fnodes_noisy = zeros(n);
Random.seed!(100)
@. fnodes_noisy  = fnodes * (1 + 1e-4 * randn()); # add Gaussian noise to each value
a_noisy=V\fnodes_noisy
@printf("||Δf||/||f|| = %g\n", norm(fnodes-fnodes_noisy)/norm(fnodes));
@printf("||Δa||/||a|| = %g\n", norm(a-a_noisy)/norm(a));

||Δf||/||f|| = 0.000102017
||Δa||/||a|| = 175.019


# Eigenvalue Problem

Find the eigenvalues of 
\begin{equation}
A = \begin{pmatrix}
1+ \delta & 0\\
0 & 1
\end{pmatrix}
\end{equation}
where $\delta>0$ is small.  First try  with the roots of the characteristic polynomial, and then try using the eigenvalue solver.  This has  characteristic polynomial
\begin{equation*}
p(z) = z^2 - (2+\delta)z + 1 + \delta
\end{equation*}

In [2]:
δ = 7e-7  # errors will appear with small values of delta
evals_exact = [1.0 + δ,1.0]
println(evals_exact)

p = z-> z^2 - (2+δ) * z + 1 + δ

evals = find_zeros(p, 0, 2)
@printf("λ₁= %.14f, λ₂= %.14f\n", evals[1],evals[2])

[1.0000007, 1.0]
λ₁= 0.99999999981527, λ₂= 1.00000069995816


In [3]:
A = [1.0 + δ 0.0;0.0 1.0]
println(A)
evals = eigvals(A)
@printf("λ₁= %.14f, λ₂= %.14f\n", evals[1],evals[2])

[1.0000007 0.0; 0.0 1.0]
λ₁= 1.00000000000000, λ₂= 1.00000070000000


# Image Compression

In [7]:
mario = load("mario.jpg");
mario_grey = float(Gray.(mario));

In [8]:
heatmap(mario_grey, yflip=true, color=:grays,colorbar=:none)

In [9]:
size(mario_grey)

(2588, 3888)

In [10]:
full_size= sizeof(mario_grey)/1e6;
@printf("%g megs\n",full_size);

40.2486 megs


In [11]:
U, S, V = svd(mario_grey);

In [25]:
k = 50;

mario_apx = U[:,1:k] * Diagonal(S[1:k]) * V[:,1:k]';
reduced_size = (sizeof( U[:,1:k]) + sizeof(S[1:k]) + sizeof( V[:,1:k]))/1e6;

@printf("Compression = %.3f%%\n",100 * reduced_size/full_size)

Compression = 3.218%


In [26]:
heatmap(mario_apx, yflip=true, color=:grays,colorbar=:none)